In [11]:
import pandas as pd
import re
import collections
from sklearn.model_selection import train_test_split
from sklearn.metrics import precision_recall_fscore_support
from nltk.corpus import stopwords
import numpy as np

In [2]:
data_df = pd.read_csv("data/training/data_train.csv", dtype='unicode')
data_df.fillna(value='', inplace=True)
data_df = data_df.apply(lambda x: x.astype(str).str.lower())

In [3]:
data_df[['clarity','conciseness']] = data_df[['clarity','conciseness']].apply(pd.to_numeric)

In [4]:
def cleanhtml(raw_html):
    result = re.sub(re.compile('<.*?>'), ' ', raw_html)
    return result
data_df['short_description_clear_html'] = data_df.apply(lambda row: cleanhtml(row['short_description']), axis=1)

In [5]:
train_df, test_df = train_test_split(data_df, test_size = 0.2)

In [6]:
full_categories_set = set()

In [7]:
for index, row in train_df.iterrows():
    full_category = row['category_lvl_1'] + "_" + row['category_lvl_2'] \
        + "_" + row['category_lvl_3']
    full_categories_set.add(full_category)

In [8]:
def create_bag_of_word(texts):
    return [ collections.Counter(re.findall(r'\w+', txt)) for txt in texts]

In [9]:
categories_word_most_frequence_dict = {}
categories_word_un_clarity_most_frequency_dict = {}
# categories_description_most_frequence_dict = {}

stopwords_set = set(stopwords.words('english'))

for full_category in full_categories_set:        

    categories = full_category.split(sep="_", maxsplit = 3)
    category_level_1 = categories[0]
    category_level_2 = categories[1]
    category_level_3 = categories[2]
    
    product_by_category = train_df[(train_df.category_lvl_1 == category_level_1) &
                                   (train_df.category_lvl_2 == category_level_2) &
                                   (train_df.category_lvl_3 == category_level_3) &
                                   (train_df.clarity == 1)]
    bag_of_words_title = create_bag_of_word([product_by_category.title.str.cat(sep=' ')])
  
    most_common_words = []
    for word, count in bag_of_words_title[0].most_common():           
        if (count > 10) & (not word.isnumeric()) & (word not in stopwords_set):
            if category_level_1 == "fashion":
                if word not in ['women', 'womens', 'girl', 'girls', 'woman'] and (count > 20):
                    most_common_words.append(word)
            else:
                most_common_words.append(word)
    
    categories_word_most_frequence_dict[full_category] = most_common_words
    
    
    bag_of_words_description = create_bag_of_word([product_by_category.short_description_clear_html.str.cat(sep=' ')])
  
    most_common_words_descrption = []
    for word, count in bag_of_words_description[0].most_common():           
        if (count > 10) & (not word.isnumeric()) & (word not in stopwords_set):
            most_common_words_descrption.append(word)
    categories_description_most_frequence_dict[full_category] = most_common_words_descrption
    

# Test model

In [12]:
clarities_pred = np.zeros(len (test_df))
categories_word_wrong_case_dict = {}

i = 0
for index, row in test_df.iterrows():
    
    full_category = row['category_lvl_1'] + "_" + row['category_lvl_2'] \
        + "_" + row['category_lvl_3']
    most_common_words_title = categories_word_most_frequence_dict.get(full_category)
    most_common_words_descrption = categories_description_most_frequence_dict.get(full_category)

    clarity_pred = 0
    for word in row['title'].split():
        if word in most_common_words_title:
            clarity_pred = 1
            break
            
#     if row['category_lvl_1'] == "fashion" and clarity_pred == 1:
#         for word in row['short_description'].split():
#             if word in most_common_words_descrption:
#                 clarity_pred = 1
#                 break   
                
    clarities_pred[i] = clarity_pred
    
            
    
    print("i = ", i)
    print ("title: ", row['title'])
    print ("descirpiton: ", row['short_description'])
    print ("Most common word: ", most_common_words_title)
    print ("full_category: ", full_category)
    print ("clarities_pred[i]: ", clarities_pred[i])
    print ("actual: ", row['clarity'])
    
    if clarities_pred[i] != row['clarity']:
        if categories_word_wrong_case_dict.get(full_category) == None:
            categories_word_wrong_case_dict[full_category] = 0
        categories_word_wrong_case_dict[full_category] += 1
    
    i = i + 1   
    

i =  0
title:  french kiss beauty hair removing wax set (tea tree, lemon, aloe vera and rose wax) and 110 wax strip paper witth free lavender water soluble wax
descirpiton:  <ul> <li>suitable for all skin type</li> <li>applicable in different season</li> <li>easily cleaned by water, without residues left on the skin</li> <li>suitable on various parts of the body</li> <li>provide a thin, economic application, suitable for use in standard cartridge wax heaters</li> <li>easy to use</li> <li>plant based extracts</li> <li>elegant design</li> </ul> 
Most common word:  ['hair', 'epilator', 'removal', 'electric']
full_category:  health & beauty_beauty tools_hair removal appliances
clarities_pred[i]:  1.0
actual:  1
i =  1
title:  king's cordless handheld rechargeable vaccum cleaner
descirpiton:  <ul> <li>cordless design; safe and reliable</li> <li>bionic cartoon style; streamlined design</li> <li>a variety of configurations; various functions within a machine</li> <li>light and flexible; easy 

descirpiton:  <ul> <li>size: 50*70 cm&nbsp;</li> <li>material: pvc</li> <li>suitable: painting surface, tile surface,&nbsp;</li> <li>glass surface, metal surface, wood surface,&nbsp;</li> </ul> 
Most common word:  ['wall', 'home', 'art', 'sticker', 'decor', 'stickers', 'room', 'decal', 'removable', 'intl', 'painting', 'diy', 'decoration', 'canvas', '3d', 'vinyl', 'mural', 'wallpaper', 'living', 'print', 'decals', 'oil', 'poster', 'export', 'picture', 'waterproof', 'bedroom', 'kids', 'modern', 'pvc', 'black', 'mirror', 'decorative', 'blue', 'multicolor', 'frameless', 'flower', 'tree', 'frame', 'new', 'cartoon', 'paper', 'white', 'awesome', 'printed', 'butterfly', 'center', 'plastic', '60x90cm', 'diamond', 'cross', 'kitchen', 'beautiful', 'house', 'stitch', 'store', 'acrylic', 'christmas', 'pattern', 'jane', 'quote', 'map', 'gift', '5d', 'nursery', 'pictures', 'window', 'creative', 'baby', 'vintage']
full_category:  home & living_home décor_wall art
clarities_pred[i]:  1.0
actual:  1
i =

full_category:  health & beauty_hair care_shampoos & conditioners
clarities_pred[i]:  1.0
actual:  1
i =  300
title:  women watches lucky star quartz watch (black) - intl
descirpiton:  <ul> <li>well designed</li> <li>100% brand new&nbsp;</li> <li>&nbsp;high quality</li> </ul> 
Most common word:  ['watch', 'women', 'quartz', 'leather', 'fashion', 'wrist', 'strap', 'watches', 'steel', 'analog', 'stainless', 'black', 'gold', 'intl', 'ladies', 'dial', 'bracelet', 'white', 'band', 'wristwatch', 'silver', 'geneva', 'diamond', 'luxury', 'casual', 'new', 'rose', 'rhinestone', 'men', 'blue', 'brand', 'waterproof', 'silicone', 'casio', 'export', 'red', 'brown', 'lady', 'womens', 'dress', 'female', 'crystal', 'faux', 'unisex', 'pink', 'elegant', 'roman', 'free', 'classic', 'pu', 'digital', 'green', 'high', 'sports', 'quality', 'case', 'couple', 'flower', 'belt', 'design', 'resin', 'business', 'kors', 'michael', 'hot', 'display', 'tone', 'vintage', 'sport', 'retro', 'numerals', 'round', 'led', 'cl

full_category:  mobiles & tablets_accessories_phone cases
clarities_pred[i]:  1.0
actual:  1
i =  465
title:  4pcs tulip flower room window curtain door sheer voile panel drapes scarfs valances
descirpiton:  <ul> <li>reasonable price</li> <li>durable and practical</li> <li>top sales item</li> <li>lovely flower curtain</li> <li>beautiful</li> <li>practical</li> <li>be used as a background for a shop window display</li> <li>creat a pretty yet modern addition for your home decor</li> </ul> 
Most common word:  ['curtain', 'window', 'door', 'curtains', 'voile', 'x', 'room', 'panel', 'drape', 'blind', 'home', 'intl']
full_category:  home & living_home décor_curtains, blinds & shades
clarities_pred[i]:  1.0
actual:  1
i =  466
title:  cherry mobile c2i with free smart sim
descirpiton:  <ul> <li>sim: dual sim</li> <li>gsm: quad band</li> <li>display: 2.8" tft lcd</li> <li>camera: 1.3mp camera</li> <li>radio: fm radio</li> <li>player: multimedia player</li> <li>bluetooth: btv2.1</li> <li>expand

actual:  1
i =  651
title:  zenfone max case, asus zenfone max case, lucky clover pu leather flip magnet wallet stand card slots case cover for asus zenfone max (zc550kl) (purple) - intl
descirpiton:  <ul> <li>high quality leather,lovely gifts</li> <li>unique lucky clover design</li> <li>a free hand strap</li> <li>with support function and slots for cards and cash</li> </ul> 
Most common word:  ['case', 'cover', 'phone', 'samsung', 'iphone', 'galaxy', 'back', 'leather', 'tpu', 'flip', 'multicolor', 'intl', 'hard', 'black', 'pu', 'plus', 'soft', 'protective', 'apple', 'pc', 'wallet', 'pattern', '6s', 'stand', 'plastic', 'huawei', 'card', 'note', 'ultra', 'hybrid', 'blue', '5s', 'armor', 'se', 'sony', 'export', 'red', 'xiaomi', 'gold', 'xperia', 'thin', 'lg', 'protector', 'amp', 'slim', 'shockproof', 'silicone', 'pink', 'shell', 'white', 'clear', 'moonmini', 'inch', 'metal', '3d', 'color', 'luxury', 'bumper', 'buildphone', 'screen', 'edge', 'htc', 'design', 'glass', 'holder', 's6', 'fram

...

Most common word:  ['controller', 'black', 'game', 'ps4', 'gamepad', 'nintendo', 'wireless', 'joystick', 'case', 'bluetooth', 'xbox', 'intl', 'cover', 'playstation', 'skin', 'white', 'sony', 'console', 'silicone', 'pc', 'remote', 'usb', 'replacement', '3ds', 'slim', 'new']
full_category:  tv, audio / video, gaming & wearables_gaming_gaming accessories
clarities_pred[i]:  1.0
actual:  1
i =  6495
title:  supercart cute flower skin case cover hard pc protector for apple iphone 6 plus 5.5" (blue)(export)
descirpiton:  <div class="prdcontent"> <ul> <li>condition:new</li> <li>material: pc</li> <li>suitable for: iphone 6 plus 5.5"</li> <li>durable hard pc back to protect your device</li> <li>precisely engineered to fit your phone perfectly</li> <li>easy to clean</li> <li>can be installed and removed by hands directly</li> </ul> </div> 
Most common word:  ['usb', 'cable', 'case', 'ipad', 'samsung', 'black', 'iphone', 'cover', 'charger', 'data', 'galaxy', 'leather', 'phone', 'intl', 'white', '

i =  6644
title:  sexy nightgown lace spa womens robes sleepwear sexy costumes bathrobe ankle-length ladies robe female nightwear(white)
descirpiton:  <ul> <li>&nbsp; &nbsp; material:chiffon</li> <li>&nbsp; &nbsp; collar:v-neck</li> <li>&nbsp; &nbsp; decroation: lace,embroidery</li> <li>&nbsp; &nbsp; size:one size</li> <li>&nbsp; &nbsp; beautiful package</li> <li>&nbsp; &nbsp; wonderful gift</li> <li>&nbsp; &nbsp; 3 colors :white/black/red</li> </ul> 
Most common word:  ['sexy', 'bra', 'lace', 'lingerie', 'black', 'waist', 'underwear', 'set', 'sleepwear', 'intl', 'dress', 'body', 'shaper', 'seamless', 'red', 'panties', 'size']
full_category:  fashion_women_lingerie, sleep & lounge
clarities_pred[i]:  1.0
actual:  0
i =  6645
title:  holbrook sunglasses 2015 new vr46 moto gp for men women sun glasses(white/orange)
descirpiton:  <div> <ul> <li>high quality men holbrook sunglasses</li> <li>plastic</li> <li>summer, spring, autumn</li> <li>cool, uv400</li> <li>outdoor/ skating/ fishing</li>

i =  6815
title:  japan.esprit black stainless-steel case leather ladies nwt + warranty es106512001
descirpiton:  <ul> <li>esprit es106512001</li> <li>38 (with crown) x 36 (w) x 8 mm (thickness)</li> <li>wr: 30m</li> <li>nwt + esprit box + warranty</li> <li>stainless-steel case</li> <li>leather</li> <li>mineral glass</li> </ul> 
Most common word:  ['watch', 'women', 'quartz', 'leather', 'fashion', 'wrist', 'strap', 'watches', 'steel', 'analog', 'stainless', 'black', 'gold', 'intl', 'ladies', 'dial', 'bracelet', 'white', 'band', 'wristwatch', 'silver', 'geneva', 'diamond', 'luxury', 'casual', 'new', 'rose', 'rhinestone', 'men', 'blue', 'brand', 'waterproof', 'silicone', 'casio', 'export', 'red', 'brown', 'lady', 'womens', 'dress', 'female', 'crystal', 'faux', 'unisex', 'pink', 'elegant', 'roman', 'free', 'classic', 'pu', 'digital', 'green', 'high', 'sports', 'quality', 'case', 'couple', 'flower', 'belt', 'design', 'resin', 'business', 'kors', 'michael', 'hot', 'display', 'tone', 'vintag

i =  6997
title:  mini silicone leather phone cover for xiaomi note (white)
descirpiton:  <ul> <li>type: phone case</li> <li>compatible phone model: xiaomi 3, xiaomi 4, xiaomi redmi, xiaomi redmi note</li> <li>color: rose red, brown, white, black, blue</li> <li>material: leather</li> <li>style: business, leisure, simple, fashion</li> <li>feature: mini invisible sucker, phone bracket, double windows</li> </ul> 
Most common word:  ['case', 'cover', 'phone', 'samsung', 'iphone', 'galaxy', 'back', 'leather', 'tpu', 'flip', 'multicolor', 'intl', 'hard', 'black', 'pu', 'plus', 'soft', 'protective', 'apple', 'pc', 'wallet', 'pattern', '6s', 'stand', 'plastic', 'huawei', 'card', 'note', 'ultra', 'hybrid', 'blue', '5s', 'armor', 'se', 'sony', 'export', 'red', 'xiaomi', 'gold', 'xperia', 'thin', 'lg', 'protector', 'amp', 'slim', 'shockproof', 'silicone', 'pink', 'shell', 'white', 'clear', 'moonmini', 'inch', 'metal', '3d', 'color', 'luxury', 'bumper', 'buildphone', 'screen', 'edge', 'htc', 'desi

Most common word:  ['case', 'cover', 'phone', 'samsung', 'iphone', 'galaxy', 'back', 'leather', 'tpu', 'flip', 'multicolor', 'intl', 'hard', 'black', 'pu', 'plus', 'soft', 'protective', 'apple', 'pc', 'wallet', 'pattern', '6s', 'stand', 'plastic', 'huawei', 'card', 'note', 'ultra', 'hybrid', 'blue', '5s', 'armor', 'se', 'sony', 'export', 'red', 'xiaomi', 'gold', 'xperia', 'thin', 'lg', 'protector', 'amp', 'slim', 'shockproof', 'silicone', 'pink', 'shell', 'white', 'clear', 'moonmini', 'inch', 'metal', '3d', 'color', 'luxury', 'bumper', 'buildphone', 'screen', 'edge', 'htc', 'design', 'glass', 'holder', 's6', 'frame', 'tempered', 'skin', 'magnetic', 'fashion', 'redmi', 'lenovo', 'mooncase', 'dual', 'full', 'slot', 'kickstand', 'rose', 'oppo', 'transparent', 'one', 'aluminum', 'silver', 'honor', 's5', 'asus', 'mobile', 'zenfone', 'layer', 's7', 'mi', 'cases', 'printing', 'painting', 'purple', 'anti', 'slots', 'heavy', 'duty', 'bling', 'mini', 'green', 'shock', 'gel', 'plate', 'brown', 'g

In [13]:
from sklearn.metrics import mean_squared_error
np.sqrt(mean_squared_error(test_df.clarity.as_matrix(), clarities_pred))

0.38055970036906306

In [14]:
max(categories_word_wrong_case_dict, key=categories_word_wrong_case_dict.get)

'fashion_women_clothing'